In [1]:
import os
import tarfile

import numpy as np
import plotly.graph_objects as go

import cuarray
import netchem
import netcalc

In [2]:
#NETSCI_ROOT=<path to netsci root directory>
NETSCI_ROOT='/home/astokely/CLionProjects/netsci'
tutorial_directory = f'{NETSCI_ROOT}/tutorial'
os.chdir(tutorial_directory)

In [3]:
tutorial_tarball = tarfile.open(f'{os.getcwd()}/tutorial.tar.gz')
tutorial_tarball.extractall()
tutorial_tarball.close()

In [4]:
r = 0.9
gaussian_2D_mean = np.zeros(2)
gaussian_2D_cov = np.array([[1.0, r], [r, 1.0]])
gaussian_2D_size = 10000

In [5]:
gaussian_2D = np.random.multivariate_normal(
    mean=gaussian_2D_mean,
    cov=gaussian_2D_cov,
    size=gaussian_2D_size,
).T.astype(np.float32)

In [6]:
gaussian_2D_figure = go.Figure(
    data=go.Scatter(
    x=gaussian_2D[0],
    y=gaussian_2D[1],
    mode='markers',
    ))

In [9]:
gaussian_2D_figure.show()

In [10]:
X = cuarray.FloatCuArray()
X.fromNumpy2D(gaussian_2D)

0

In [11]:
ab = cuarray.IntCuArray()

In [12]:
ab.init(1, 2)
ab[0][0] = 0
ab[0][1] = 1

In [13]:
I = cuarray.FloatCuArray()

In [14]:
n = gaussian_2D_size
k = 4
xd = 2
d = 1
platform = "gpu"

In [15]:
netcalc.mutualInformation(
    X=X,
    I=I, 
    ab=ab,
    k=k,
    n=n,
    xd=xd,
    d=d,
    platform=platform,
)

In [16]:
print(I)

0.8364


In [17]:
analytic_I = -0.5*np.log(np.linalg.det(np.cov(gaussian_2D)))
print(analytic_I)

0.8198339037028032


In [18]:
pyro_graph = netchem.Graph()

In [19]:
trajectory_file = f'{os.getcwd()}/pyro.dcd'
topology_file = f'{os.getcwd()}/pyro.pdb'
first_frame = 0
last_frame = 999
pyro_graph.init(
    trajectoryFile=trajectory_file,
    topologyFile=topology_file,
    firstFrame=first_frame,
    lastFrame=last_frame,
)

In [20]:
pyro_R = cuarray.FloatCuArray()
pyro_ab = cuarray.IntCuArray()

In [21]:
pyro_num_nodes = pyro_graph.numNodes()
pyro_num_node_pairs = pyro_num_nodes**2
pyro_ab.init(
    pyro_num_node_pairs,
    2,
)
for i in range(pyro_num_nodes):
    for j in range(pyro_num_nodes):
        pyro_node_pair_index = i*pyro_num_nodes + j
        pyro_ab[pyro_node_pair_index][0] = i
        pyro_ab[pyro_node_pair_index][1] = j

In [22]:
pyro_n = pyro_graph.numFrames()
pyro_d = 3
pyro_xd = 2
pyro_k = 4
pyro_platform = "gpu"

In [23]:
netcalc.generalizedCorrelation(
    X=pyro_graph.nodeCoordinates(),
    R=pyro_R,
    ab=pyro_ab,
    k=pyro_k,
    n=pyro_n,
    d=pyro_d,
    xd=pyro_xd,
    platform=pyro_platform,
)

In [24]:
pyro_R_np = pyro_R.toNumpy2D().reshape(
    pyro_num_nodes,
    pyro_num_nodes,
)

In [25]:
pyro_R_figure_x = [i for i in range(pyro_num_nodes)]
pyro_R_figure_y = [i for i in range(pyro_num_nodes)]

In [26]:
pyro_R_figure = go.Figure(
    data=go.Heatmap(
        x=pyro_R_figure_x,
        y=pyro_R_figure_y,
        z=pyro_R_np,
        colorscale='jet',
        zsmooth='best',
    ),
)

In [27]:
pyro_R_figure.show()

In [28]:
pyro_A = cuarray.FloatCuArray()
pyro_paths = cuarray.IntCuArray()
pyro_H = cuarray.FloatCuArray()

In [29]:
netcalc.correlationToAdjacency(
    A=pyro_A,
    C=pyro_R,
    n=pyro_num_nodes,
    platform=pyro_platform,
)

In [30]:
netcalc.hedetniemiShortestPaths(
    A=pyro_A,
    H=pyro_H,
    paths=pyro_paths,
    tolerance=0.0004,
    platform=pyro_platform,
)

In [31]:
for i in range(pyro_num_nodes):
    for j in range(pyro_num_nodes):
        ssp = netcalc.pathFromPathsCuArray(
            paths=pyro_paths,
            i=i,
            j=j,
        )
        print(ssp, i, j)


[0] 0 0
[0 1] 0 1
[0 2] 0 2
[0 3] 0 3
[0 4] 0 4
[0 5] 0 5
[0 6] 0 6
[0 7] 0 7
[0 8] 0 8
[0 9] 0 9
[ 0 10] 0 10
[ 0 11] 0 11
[ 0 12] 0 12
[ 0 13] 0 13
[ 0 14] 0 14
[ 0 15] 0 15
[ 0 16] 0 16
[ 0 17] 0 17
[ 0 18] 0 18
[ 0 19] 0 19
[ 0 20] 0 20
[ 0 21] 0 21
[ 0 22] 0 22
[ 0 23] 0 23
[ 0 24] 0 24
[ 0 25] 0 25
[ 0 26] 0 26
[ 0 27] 0 27
[ 0 28] 0 28
[ 0 29] 0 29
[ 0 30] 0 30
[ 0 31] 0 31
[ 0 32] 0 32
[ 0 33] 0 33
[ 0 34] 0 34
[ 0 35] 0 35
[ 0 36] 0 36
[ 0 37] 0 37
[ 0 38] 0 38
[ 0 39] 0 39
[ 0 40] 0 40
[ 0 41] 0 41
[ 0 42] 0 42
[ 0 43] 0 43
[ 0 44] 0 44
[ 0 45] 0 45
[ 0 46] 0 46
[ 0 47] 0 47
[ 0 48] 0 48
[ 0 49] 0 49
[ 0 50] 0 50
[ 0 51] 0 51
[ 0 52] 0 52
[ 0 53] 0 53
[ 0 54] 0 54
[ 0 55] 0 55
[ 0 56] 0 56
[ 0 57] 0 57
[ 0 58] 0 58
[ 0 59] 0 59
[ 0 60] 0 60
[ 0 61] 0 61
[ 0 62] 0 62
[ 0 63] 0 63
[ 0 64] 0 64
[ 0 65] 0 65
[ 0 66] 0 66
[ 0 67] 0 67
[ 0 68] 0 68
[ 0 69] 0 69
[ 0 70] 0 70
[ 0 71] 0 71
[ 0 72] 0 72
[ 0 73] 0 73
[ 0 74] 0 74
[ 0 75] 0 75
[ 0 76] 0 76
[ 0 77] 0 77
[ 0 78] 0 78
[ 0 7

In [32]:
for i in range(pyro_num_nodes):
    for j in range(pyro_num_nodes):
        ssp = netcalc.pathFromPathsCuArray(
            paths=pyro_paths,
            i=i,
            j=j,
        )
        if len(ssp) > 2:
            print(ssp, i, j)

[  0 142 141] 0 141
[ 3 37 36] 3 36
[  3 146 144] 3 144
[  3 146 145] 3 145
[  3 142 155] 3 155
[ 4 37 36] 4 36
[  4 142 141] 4 141
[  4 146 144] 4 144
[  5 288 156] 5 156
[  6 146 145] 6 145
[  7 223  98] 7 98
[  9 267  31] 9 31
[  9 223  98] 9 98
[  9 105 107] 9 107
[  9 288 199] 9 199
[ 10 267  31] 10 31
[ 10 266  32] 10 32
[10 62 66] 10 66
[ 10 173 140] 10 140
[ 10  12 144] 10 144
[ 10 288 199] 10 199
[ 10 287 241] 10 241
[ 13 142 155] 13 155
[ 13 233 251] 13 251
[16 21 31] 16 31
[ 16 124 157] 16 157
[ 16 227 226] 16 226
[17 37 36] 17 36
[17 63 65] 17 65
[ 17 263 109] 17 109
[ 17 173 140] 17 140
[ 17 287 144] 17 144
[ 17 267 156] 17 156
[ 17 263 158] 17 158
[ 17 288 199] 17 199
[ 17 239 241] 17 241
[18 33 32] 18 32
[ 18 146 145] 18 145
[ 18 242 241] 18 241
[ 18 233 251] 18 251
[19 20 31] 19 31
[ 19 269  84] 19 84
[ 19 223  98] 19 98
[ 19 263 109] 19 109
[ 19  95 121] 19 121
[ 19  21 141] 19 141
[ 19 287 144] 19 144
[ 19 288 145] 19 145
[ 19 286 192] 19 192
[ 19 269 196] 19 196
[ 19

In [33]:
for i in range(pyro_num_nodes):
    for j in range(pyro_num_nodes):
        ssp = netcalc.pathFromPathsCuArray(
            paths=pyro_paths,
            i=i,
            j=j,
        )
        rij = pyro_R_np[i,j]
        if len(ssp) > 2:
            print(ssp, i, j, rij)

[  0 142 141] 0 141 0.24377206
[ 3 37 36] 3 36 0.22388561
[  3 146 144] 3 144 0.22760022
[  3 146 145] 3 145 0.19957925
[  3 142 155] 3 155 0.21506101
[ 4 37 36] 4 36 0.22598548
[  4 142 141] 4 141 0.24353588
[  4 146 144] 4 144 0.24278554
[  5 288 156] 5 156 0.21828753
[  6 146 145] 6 145 0.21837488
[  7 223  98] 7 98 0.25899568
[  9 267  31] 9 31 0.2209238
[  9 223  98] 9 98 0.22633429
[  9 105 107] 9 107 0.24618843
[  9 288 199] 9 199 0.28661776
[ 10 267  31] 10 31 0.20499818
[ 10 266  32] 10 32 0.19290848
[10 62 66] 10 66 0.24416858
[ 10 173 140] 10 140 0.25360182
[ 10  12 144] 10 144 0.24804063
[ 10 288 199] 10 199 0.29154214
[ 10 287 241] 10 241 0.24153492
[ 13 142 155] 13 155 0.22841048
[ 13 233 251] 13 251 0.25262326
[16 21 31] 16 31 0.17044339
[ 16 124 157] 16 157 0.21950428
[ 16 227 226] 16 226 0.2509186
[17 37 36] 17 36 0.21524704
[17 63 65] 17 65 0.24866402
[ 17 263 109] 17 109 0.23679627
[ 17 173 140] 17 140 0.10661289
[ 17 287 144] 17 144 0.17949484
[ 17 267 156] 17 156 0